In [185]:
import pandas as pd
import geopandas as gpd
import folium

# Read GeoJson data: Helsingin peruspiirijako A_HK_PER
fname = 'a_hk_per.json'
df = gpd.read_file(fname)
# df.head()

In [186]:
# Read building data from csv
data = pd.read_csv('./kokotun.csv')
# data.head()

In [187]:
# Make our dataset to use the newest data from 2016: 
ndata = data[['None','2016', '2016.1', '2016.2', '2016.3', '2016.4', '2016.5', '2016.6', '2016.7', '2016.8', '2016.9', '2016.10', '2016.11', '2016.12', '2016.13', '2016.14', '2016.15', '2016.16', '2016.17', '2016.18', '2016.19', '2016.20', '2016.21', '2016.22', '2016.23', '2016.24', '2016.25', '2016.26', '2016.27', '2016.28', '2016.29', '2016.30', '2016.31', '2016.32', '2016.33', '2016.34', '2016.35', '2016.36', '2016.37', '2016.38', '2016.39', '2016.40', '2016.41', '2016.42', '2016.43', '2016.44', '2016.45', '2016.46', '2016.47', '2016.48', '2016.49', '2016.50', '2016.51', '2016.52', '2016.53', '2016.54', '2016.55', '2016.56', '2016.57', '2016.58', '2016.59', '2016.60', '2016.61', '2016.62', '2016.63', '2016.64']].copy()

# Rename first row to kokotun:
ndata.rename(columns={'None':'kokotun'}, inplace=True)

# Remove rows that are not on the map: 
ndata = ndata[ndata['kokotun'].isin(df.KOKOTUN.tolist())]

# Reset dataframe index:
ndata = ndata.reset_index(drop=True)
#print(ndata)

In [188]:
# Classify each row as follows:
#1: Detached- and semi-detached houses (erilaiset pientalot)
#2: Attached houses (rowhouses, terraced houses; rivi- ja ketjutalot)
#3: Blocks of Flats (asuinkerrostalot, luhtitalot)
#4: Other blocks of flats (muut asuinkerrostalot)
# index = position of the number on the row
# row = data frame row of items
def classify(index, row):
    first = int(row[index])
    second = int(row[index+1])
    third = int(row[index+2])
    fourth = int(row[index+3])
    
    list = [first, second, third, fourth]
    
    biggest = max(list)
    
    # Classify 
    #if(biggest==0):
    #    return 0
    if (biggest == first):
        return 1
    if(biggest == second):
        return 2
    if(biggest == third):
        return 3
    if(biggest == fourth):
        return 4

# Run classifier for all wanted categories and append the colors to df_colors dataframe.
# index = index of the first wanted item on the row
# title = title of the new dataframe column
def addcolorstodataframe(title, index):
    global df_colors
    dict = []
    
    # Append to dict a primary color for each area by fetching each kokotun-number and 
    # classifying the row with classify-function
    for x in range(0,34):
        dict.append([ndata.take([x]).values.tolist()[0][0], classify(index, ndata.take([x]).values.tolist()[0])])
        
    # Create a temporary dataframe with the kokotun and year data
    df_temp = pd.DataFrame(dict, columns = ['kokotun', title])
    # Set the index just in case 
    df_temp = df_temp.set_index(df_colors.index)
    # Merge the temporary dataframe into df_colors
    df_colors = pd.merge(df_colors, df_temp, on='kokotun')

In [189]:
# Create a dataframe for collecting color data:
df_colors=pd.DataFrame(columns=['kokotun'])
df_colors['kokotun'] = ndata['kokotun']
print(df_colors.shape)

# Create a dataframe that contains colors for each year group: 
# Ranges contains the title of the dataframe and index of the wanted placement: 
ranges = {'-1920':7, '21-29':12, '30-39':17, '40-49':22, '50-59':27,
          '60-69':32, '70-79':37, '80-89':42, '90-99':47, '00-09':52,
          '10-16':57, 'total':2}

for title, index in ranges.items():
    addcolorstodataframe(title, index)
    
#print(df_colors)

(34, 1)


In [190]:
# Draw a folium map of the data:

# -1920

map20 = folium.Map([60.192059, 24.945831], zoom_start=10)

map20.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '-1920'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )
map20

1: Detached- and semi-detached houses (erilaiset pientalot)

2: Attached houses (rowhouses, terraced houses; rivi- ja ketjutalot)

3: Blocks of Flats (asuinkerrostalot, luhtitalot)

4: Other blocks of flats (muut asuinkerrostalot)

In [191]:
# 1921-1929

map29 = folium.Map([60.192059, 24.945831], zoom_start=10)

map29.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '21-29'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map29

In [192]:
# 1930-1939

map39 = folium.Map([60.192059, 24.945831], zoom_start=10)

map39.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '30-39'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map39

In [193]:
# 1940-1949

map49 = folium.Map([60.192059, 24.945831], zoom_start=10)

map49.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '40-49'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map49

In [194]:
# 1950-1959

map59 = folium.Map([60.192059, 24.945831], zoom_start=10)

map59.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '50-59'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map59

In [195]:
# 1960-1969

map69 = folium.Map([60.192059, 24.945831], zoom_start=10)

map69.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '60-69'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map69

In [196]:
# 1970-1979

map79 = folium.Map([60.192059, 24.945831], zoom_start=10)

map79.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '70-79'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map79

In [197]:
# 1980-1989

map89 = folium.Map([60.192059, 24.945831], zoom_start=10)

map89.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '80-89'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map89

In [198]:
# 1990-1999

map99 = folium.Map([60.192059, 24.945831], zoom_start=10)

map99.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '90-99'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map99

In [199]:
# 2000-2009

map09 = folium.Map([60.192059, 24.945831], zoom_start=10)

map09.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '00-09'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map09

In [200]:
# 2010-2016

map16 = folium.Map([60.192059, 24.945831], zoom_start=10)

map16.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', '10-16'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )

map16

In [201]:
m_tot = folium.Map([60.192059, 24.945831], zoom_start=10)

m_tot.choropleth(
    geo_data=fname,
    data=df_colors,
    columns=['kokotun', 'total'],
    key_on='properties.KOKOTUN',
    fill_color='YlGnBu', 
    fill_opacity=0.8, line_opacity=0.4,
    highlight=True,
    threshold_scale=[1, 2, 3, 4]
    )
m_tot